## Text Classification
Project Aim : To classify a given document into a category.

## Building Vocabulary
Before applying any kind of algorithm, we first build the vocabulory, that is getting the data ready in the desired form/shape.

In [1]:
# Imports
import os
from nltk.corpus import stopwords
import string
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split

### Feature Extraction 

In [2]:
DATASET_PATH = '20_newsgroups'

# List of folders that will be used later
folders = [folder for folder in os.listdir(DATASET_PATH)]

In [3]:
# 2D list of files, where ith index will store all filenames in the ith folder
files = []
for folder in folders:
    # Create paths to subdirectories
    folder_path = os.path.join(DATASET_PATH, folder)
    # Add all files in current folder to the list
    files.append([file for file in os.listdir(folder_path)])

# Total files 
sum(len(files[i]) for i in range(20))

19997

In [4]:
# List of pathnames to all files in our dataset
pathname_list = []
# For each folder
for folder in range(len(folders)):
    # For all files in current folder
    for file in files[folder]:
        # add path to pathname list
        pathname_list.append(os.path.join(DATASET_PATH, os.path.join(folders[folder], file)))

# check if all files path have been added
len(pathname_list)

19997

In [5]:
# Y array - this holds the output class for each document
Y = []
for folder in folders:
    folder_path = os.path.join(DATASET_PATH, folder)
    num_files = len(os.listdir(folder_path))
    # Add Y = name of folder for all files in current folder
    for i in range(num_files):
        Y.append(folder)

# Checking if all files have been given a category
len(Y)

19997

#### Splitting data into train and test

In [6]:
X_train, X_test, Y_train, Y_test = train_test_split(pathname_list, Y, random_state=42)
len(X_train), len(X_test), len(Y_train), len(Y_test)

(14997, 5000, 14997, 5000)

### Word Extraction from document

In [7]:
# Function to process a file and extract words from it
def preprocess_words(words): 
    
    # removing punctuation from each word
    mapping_table = str.maketrans('', '', string.punctuation)

    # clean words
    words = [w.translate(mapping_table) for w in words]

    # normalizing case - making all words of the same case
    words = [w.lower() for w in words]

    # removing any blank words that may have been left due to nature of the dataset
    words = [w for w in words if w] # if the word has some length then store else remove

    # removing numeric strings as they don't add that much value to our dataset
    words = [w for w in words if not w.isdigit()]

    # removing words with single character or two characters
    words = [w for w in words if len(w) > 2]
    
    return words

In [8]:
# Function to remove stop words
def remove_stopwords(words):
    stop_words = set(stopwords.words('english')) 
    block_words = ['newsgroups', 'xref', 'path', 'from', 'subject', 'sender', 'organisation', 'apr','gmt', 'last','better','never','every','even','two','good','used','first','need','going','must','really','might','well','without','made','give','look','try','far','less','seem','new','make','many','way','since','using','take','help','thanks','send','free','may','see','much','want','find','would','one','like','get','use','also','could','say','us','go','please','said','set','got','sure','come','lot','seems','able','anything','put', '--', '|>', '>>', '93', 'xref', 'cantaloupe.srv.cs.cmu.edu',
                   '20', '16', "max>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'ax>'", '21', '19', '10', '17', '24', 
                   'reply-to:', 'thu', 'nntp-posting-host:', 're:','25''18'"i'd"'>i''22''fri,''23''>the',
                   'references:','xref:','sender:','writes:','1993','organization:']
    return [w for w in words if not w in stop_words and not w in block_words]

In [9]:
# Function to remove metadata above each line

# The metadata for each document ends at the first occurence of a blank line

def remove_metadata(lines):
    # iterate over all lines
    for i in range(len(lines)):
        if lines[i]=='\n':
            # Blank line found
            start = i + 1
            break
    # discard data before the start valued line
    new_lines = lines[start:]
    return new_lines

In [10]:
# Function to convert a line into a list of words
def tokenize_line(line):
    # Splitting the line at each space encountered
    words = line[0:len(line)-1].strip().split(" ")
    
    # preprocess words
    words = preprocess_words(words)
    
    # remove stopwords
    words = remove_stopwords(words)
    
    return words

In [11]:
# Function to convert a document into list of words
def tokenize_doc(file_path):
    
    # Load document
    doc = open(file_path, 'r', encoding="ISO-8859-1")
    doc_lines = doc.readlines()
    
    # Remove metadata
    doc_lines = remove_metadata(doc_lines)
    
    # Intializing empty words array for doc
    doc_words = []
    
    for line in doc_lines:
        doc_words.append(tokenize_line(line))
    
    return doc_words

In [12]:
# Flatten the list of words i.e, 2D to 1D
def flatten(words):
    new_words = []
    for i in words:
        for j in i:
            new_words.append(j)
    return new_words

### Working on actual data

In [13]:
list_of_words = []
for doc in X_train:
    list_of_words.append(flatten(tokenize_doc(doc)))

#### List of words is a 2D array, where each row has words for that doc. And on flattening we get the complete vocabulary

In [14]:
# Converting the list of words to a numpy array
np_words = np.asarray(flatten(list_of_words))
np_words.shape

(1795356,)

In [15]:
# Number of unique words
words, counts = np.unique(np_words, return_counts=True)
len(words)

147032

In [16]:
# Sorting the unique words on basis of count and storing them in two lists
# one list holds the actual word and the other holds count of that word
freq, words_ = (list(i) for i in zip(*(sorted(zip(counts, words), reverse=True))))

### Transforming training data into proper shape

In [17]:
num_words_selected = 12300
features = words_[0:num_words_selected]
print(features)

['writes', 'article', 'dont', 'people', 'know', 'think', 'time', 'right', 'system', 'god', 'anyone', 'work', 'something', 'believe', 'still', 'problem', 'ive', 'back', 'email', 'point', 'information', 'government', 'years', 'file', 'cant', 'things', 'doesnt', 'question', 'another', 'read', 'someone', 'year', 'thing', 'thats', 'etc', 'maxaxaxaxaxaxaxaxaxaxaxaxaxaxax', 'number', 'fact', 'windows', 'university', 'available', 'part', 'drive', 'around', 'world', 'data', 'power', 'program', 'didnt', 'case', 'different', 'little', 'however', 'law', 'best', 'long', 'probably', 'least', 'day', 'actually', 'true', 'enough', 'course', 'software', 'space', 'tell', 'game', 'state', 'car', 'computer', 'great', 'though', 'says', 'either', 'david', 'nothing', 'mean', 'jesus', 'real', 'life', 'rather', 'youre', 'possible', 'group', 'others', 'support', 'run', 'called', 'reason', 'second', 'else', 'wrong', 'let', 'call', 'name', 'hard', 'yes', 'john', 'list', 'place', 'keep', 'old', 'done', 'seen', 'fou

### Building the vocabulary dictionary

In [18]:
# This dictionary will hold the vocabulory for each document and will help us build the training set later
# dict[doc][word] symbolised that a particular document has in it a particular words and the value of the key 
# is the frequency of that word in that particular doc
vocab = {}
curr_doc = 1
for curr_doc_words in list_of_words:
    vocab[curr_doc] = {}
    np_curr_doc_words = np.asarray(curr_doc_words)
    words_in_curr_doc, frequencies = np.unique(np_curr_doc_words, return_counts=True)
    for i in range(len(words_in_curr_doc)):
        # Add each words count for current doc
        vocab[curr_doc][words_in_curr_doc[i]] = frequencies[i]
    curr_doc = curr_doc + 1

vocab

{1: {'1993apr2616362711364csrduiucedu': 1,
  'abortion': 2,
  'afford': 2,
  'arise': 1,
  'article': 1,
  'birth': 3,
  'cant': 2,
  'case': 1,
  'choice': 1,
  'conlon': 1,
  'doesnt': 1,
  'done': 1,
  'evelyn': 1,
  'expensive': 1,
  'frank': 1,
  'gskinneruiucedu': 1,
  'hardly': 1,
  'hatching': 1,
  'hens': 1,
  'latter': 1,
  'meaning': 1,
  'mother': 2,
  'objection': 1,
  'odwyer': 1,
  'odwyersseie': 1,
  'parker': 1,
  'pay': 1,
  'paying': 1,
  'pregnancy': 3,
  'refused': 1,
  'sense': 1,
  'sensible': 1,
  'skinner': 1,
  'statement': 1,
  'statements': 1,
  'together': 1,
  'topic': 1,
  'unable': 1,
  'ways': 1,
  'writes': 1},
 2: {'\tyou': 1,
  '1ren9a94qmorrowstanfordedu': 1,
  '2nd': 1,
  'accept': 1,
  'actual': 2,
  'ago': 1,
  'altogether': 1,
  'ancient': 1,
  'anonymous': 2,
  'another': 2,
  'appear': 1,
  'applies': 1,
  'apply': 1,
  'aramaic': 1,
  'around': 1,
  'article': 2,
  'associates': 2,
  'assuredly': 1,
  'attempt': 1,
  'attested': 1,
  'backgro

### Using Vocab to build training dataset into 2D shape

In [19]:
# Building a 2D array as our training data using vocabulory
# First 7000 words will be treated as features, ith row will have the frequency of each of those features for 
# the ith doc
X_train_final = []
for key in vocab.keys():
    curr_doc_row = []
    for word in features:
        # if word present in vocab of curr_doc add it in training set
        if word in vocab[key].keys():
            curr_doc_row.append(vocab[key][word])
        # else put value as 0
        else:
            curr_doc_row.append(0)
    # add curr_doc row to training set
    X_train_final.append(curr_doc_row)

In [20]:
# Casting arrays to numpy arrays
X_train_final = np.asarray(X_train_final)
Y_train = np.asarray(Y_train)

In [21]:
X_train_final.shape, Y_train.shape

((14997, 12300), (14997,))

In [22]:
# Making a dataframe for better representation of data
df = pd.DataFrame(X_train_final)
df.columns = features
df.head()

writes  article  dont  people  know  think  time  right  system  god  \
0       1        1     0       0     0      0     0      0       0    0   
1       3        2     0       1     1      1     2      0       0    0   
2       0        1     0       0     0      1     0      0       0    0   
3       2        1     0       0     0      0     0      0       0    0   
4       0        0     0       0     0      0     0      0       0    0   

     ...      waits  wailing  wagons  vomiting  vols  visually  vii  \
0    ...          0        0       0         0     0         0    0   
1    ...          0        0       0         0     0         0    0   
2    ...          0        0       0         0     0         0    0   
3    ...          0        0       0         0     0         0    0   
4    ...          0        0       0         0     0         0    0   

   viability  verbeek  venerable  
0          0        0          0  
1          0        0          0  
2          0        0          0  
3          0        0          0  
4          0        0          0  

[5 rows x 12300 columns]

### Preparing Test Data
Now that our training data is prepared , we will prepare the test data in a similar manner

In [23]:
list_of_words_test = []
for doc in X_test:
    list_of_words_test.append(flatten(tokenize_doc(doc)))

len(list_of_words_test)

5000

In [24]:
vocab_test = {}
curr_doc = 1
for curr_doc_words in list_of_words_test:
    vocab_test[curr_doc] = {}
    np_curr_doc_words = np.asarray(curr_doc_words)
    words_in_curr_doc, frequencies = np.unique(np_curr_doc_words, return_counts=True)
    for i in range(len(words_in_curr_doc)):
        # Add each words count for current doc
        vocab_test[curr_doc][words_in_curr_doc[i]] = frequencies[i]
    curr_doc = curr_doc + 1

vocab_test

{1: {'3point': 1,
  'agree': 1,
  'along': 1,
  'andrew': 1,
  'andrewfripwvtekcom': 1,
  'attack': 1,
  'back': 2,
  'belts': 2,
  'best': 1,
  'cargo': 1,
  'class': 1,
  'controversial': 1,
  'copies': 1,
  'cravanvoyager': 1,
  'eliminating': 1,
  'extra': 1,
  'ill': 1,
  'instead': 1,
  'killed': 1,
  'klossner': 1,
  'leg': 1,
  'mazda': 1,
  'middle': 1,
  'mpv': 2,
  'price': 1,
  'rear': 1,
  'room': 1,
  'seat': 3,
  'shoehorned': 1,
  'shove': 1,
  'small': 1,
  'space': 1,
  'suv': 1,
  'villager': 2,
  'villagerquest': 1},
 2: {'1993apr1703152013902clarinetcom': 1,
  'actual': 1,
  'algorithm': 1,
  'article': 1,
  'brad': 1,
  'bradclarinetcom': 1,
  'cellular': 1,
  'classified': 1,
  'decryption': 1,
  'doesnt': 1,
  'encrypting': 1,
  'encryption': 1,
  'end': 5,
  'hence': 1,
  'however': 1,
  'kept': 1,
  'keys': 1,
  'later': 1,
  'link': 1,
  'main': 1,
  'means': 1,
  'phones': 1,
  'radio': 2,
  'secure': 1,
  'sense': 1,
  'telco': 1,
  'templeton': 1,
  'think

In [25]:
#2D test dataset making
X_test_final = []
for key in vocab_test.keys():
    curr_doc_row = []
    for word in features:
        # if word present in vocab of curr_doc add it in training set
        if word in vocab_test[key].keys():
            curr_doc_row.append(vocab_test[key][word])
        # else put value as 0
        else:
            curr_doc_row.append(0)
    # add curr_doc row to training set
    X_test_final.append(curr_doc_row)

In [26]:
# Casting arrays to numpy arrays
X_test_final = np.asarray(X_test_final)
Y_test = np.asarray(Y_test)

In [27]:
X_test_final.shape, Y_test.shape

((5000, 12300), (5000,))

In [28]:
# Making a dataframe for better representation of data
df = pd.DataFrame(X_test_final)
df.columns = features
df.head()

writes  article  dont  people  know  think  time  right  system  god  \
0       0        0     0       0     0      0     0      0       0    0   
1       1        1     0       0     0      1     0      0       0    0   
2       1        1     0       0     0      0     0      0       0    0   
3       0        0     0       0     0      0     1      0       0    0   
4       0        0     0       0     1      0     0      0       0    0   

     ...      waits  wailing  wagons  vomiting  vols  visually  vii  \
0    ...          0        0       0         0     0         0    0   
1    ...          0        0       0         0     0         0    0   
2    ...          0        0       0         0     0         0    0   
3    ...          0        0       0         0     0         0    0   
4    ...          0        0       0         0     0         0    0   

   viability  verbeek  venerable  
0          0        0          0  
1          0        0          0  
2          0        0          0  
3          0        0          0  
4          0        0          0  

[5 rows x 12300 columns]

### Text Classification (Using Naive Bayes - Multinomial)

#### Using Sklearn Inbuilt Naive Bayes

In [29]:
from sklearn.naive_bayes import MultinomialNB
clf = MultinomialNB()

In [30]:
# fit on our data
clf.fit(X_train_final, Y_train)

MultinomialNB(alpha=1.0, class_prior=None, fit_prior=True)

In [31]:
Y_pred = clf.predict(X_test_final)

In [32]:
Y_pred.shape

(5000,)

In [33]:
clf.score(X_test_final, Y_test)

0.8024

In [34]:
from sklearn.metrics import classification_report, confusion_matrix

In [35]:
print(classification_report(Y_test, Y_pred))

                          precision    recall  f1-score   support

             alt.atheism       0.64      0.79      0.71       256
           comp.graphics       0.72      0.76      0.74       251
 comp.os.ms-windows.misc       0.73      0.73      0.73       247
comp.sys.ibm.pc.hardware       0.69      0.73      0.71       237
   comp.sys.mac.hardware       0.77      0.78      0.78       254
          comp.windows.x       0.80      0.81      0.80       242
            misc.forsale       0.87      0.77      0.82       271
               rec.autos       0.87      0.86      0.87       252
         rec.motorcycles       0.89      0.94      0.92       237
      rec.sport.baseball       0.93      0.95      0.94       242
        rec.sport.hockey       0.97      0.96      0.96       261
               sci.crypt       0.94      0.89      0.91       253
         sci.electronics       0.78      0.76      0.77       247
                 sci.med       0.92      0.87      0.90       269
         

In [36]:
print(confusion_matrix(Y_test, Y_pred))

[[202   1   0   0   0   1   0   1   1   0   1   0   0   3   0  12   1   5
    3  25]
 [  0 190  22   9   5  11   3   0   0   1   0   0   0   2   4   0   0   0
    2   2]
 [  0  12 181  18   2  16   2   3   1   1   0   1   2   0   0   0   1   0
    5   2]
 [  0   6  19 174  19   1   7   1   0   0   0   0   9   1   0   0   0   0
    0   0]
 [  0   4   7  21 198   1   5   2   1   1   0   0   8   2   1   0   1   0
    2   0]
 [  1  24   5   7   3 195   0   0   0   2   0   2   1   0   0   0   0   1
    0   1]
 [  0   1   3  11  10   0 210  10   5   0   2   1  10   0   5   0   0   0
    3   0]
 [  3   1   1   0   0   3   4 217   7   1   1   0   7   0   1   0   4   0
    2   0]
 [  0   0   0   0   0   1   4   4 223   0   0   0   2   1   0   0   0   0
    2   0]
 [  0   1   0   0   1   2   1   0   2 229   3   0   0   0   0   2   0   0
    1   0]
 [  1   0   1   1   0   0   0   0   0   5 250   0   1   0   0   1   0   0
    1   0]
 [  0   1   3   0   1   3   0   0   1   0   0 225   0   0   0   1

In [37]:
# Score on training data
clf.score(X_train_final, Y_train)

0.8841101553644062

#### Self Implemented

In [38]:
# Self implementation of Multinomial Naive Bayes

In [39]:
# Fit function - this function will make the count dicitionary for us

# The dicitonary will hold the count of words for all distinct classes (not all documents)

# This dictionary will then be used to predict on the testing data

def fit(x, y):
    # Initializing with an empty dictionary
    result = {}
    classes = set(y)
    # Total data points
    result["total_data"] = len(y)
    
    for curr_class in classes:
        # Make a deeper level for current class
        result[curr_class] = {}
        # Rows where Y = curr_class
        current_class_rows = (y == curr_class)
        # Arrays with data for only curr_class
        X_curr_class = x[current_class_rows]
        Y_curr_class = y[current_class_rows]
        num_features = len(features) # Number of words selected to be features
        
        # for each word in features 
        for i in range (0, num_features):
            # Take sum of current words for all documents with output as current class
            result[curr_class][features[i]] = X_curr_class[:, i].sum()
        # Total word count for current class
        result[curr_class]["total_count"] = len(Y_curr_class)
    return result

In [40]:
# probability Function - this function will calculate log probabilities for all classes for a document using
# the dictionary made by the fit function

def probability(doc, dictionary, curr_class):
    
    # Probability that Y = curr_class
    output_prob = np.log(dictionary[curr_class]["total_count"]) - np.log(dictionary["total_data"])
    num_features = len(features) - 1 # -1 for total_data key
    # for each word in the dataset 
    for i in range (0, num_features):
        # Counts with laplace corrections
        count_word_curr_class = dictionary[curr_class][features[i]] + 1
        count_curr_class = dictionary[curr_class]["total_count"] + len(features)
        curr_word_curr_class_prob = np.log(count_word_curr_class) - np.log(count_curr_class)
        # adding the probability of the word the number of times it occurs in the current document
        for j in range(int(doc[i])):
            output_prob += curr_word_curr_class_prob
    print(output_prob)
    return output_prob

In [41]:
# predictSinglePoint function - this function will predict the output for a single document at a time

def predictSinglePoint(doc, dictionary):
    # Possible classes
    classes = dictionary.keys()
    # Some initialization paramaters
    best_p = -1000
    best_class = -1
    first_run = True
    # iterate over all classes
    for curr_class in classes:
        # if all classes exhausted
        if curr_class == "total_data":
            continue
        # Calculate probability of curr_class being output for the current data point
        p_curr_class = probability(doc, dictionary, curr_class)
        # if it is better than current best probability - update
        if (p_curr_class > best_p or first_run):
            best_p = p_curr_class
            best_class = curr_class
        first_run = False
    return best_class

In [42]:
# Predict Function - Will make the prediction using the dictionary that the fit function will build

def predict(x_test, dictionary):
    
    # We'll make a prediction for each document in the test data
    Y_pred = []
    j = 1
    for doc in x_test:
        print(j)
        j += 1
        doc_class = predictSinglePoint(doc, dictionary)
        Y_pred.append(doc_class)
    return Y_pred

## Training on self implemented multinomial NB

In [43]:
dictionary = fit(X_train_final, Y_train)

In [44]:
dictionary

{'total_data': 14997,
 'sci.electronics': {'writes': 453,
  'article': 367,
  'dont': 275,
  'people': 98,
  'know': 319,
  'think': 138,
  'time': 178,
  'right': 83,
  'system': 115,
  'god': 7,
  'anyone': 237,
  'work': 188,
  'something': 126,
  'believe': 35,
  'still': 87,
  'problem': 131,
  'ive': 158,
  'back': 86,
  'email': 99,
  'point': 71,
  'information': 108,
  'government': 2,
  'years': 66,
  'file': 17,
  'cant': 68,
  'things': 84,
  'doesnt': 65,
  'question': 98,
  'another': 67,
  'read': 71,
  'someone': 71,
  'year': 32,
  'thing': 104,
  'thats': 60,
  'etc': 106,
  'maxaxaxaxaxaxaxaxaxaxaxaxaxaxax': 0,
  'number': 90,
  'fact': 36,
  'windows': 19,
  'university': 97,
  'available': 50,
  'part': 70,
  'drive': 64,
  'around': 114,
  'world': 22,
  'data': 121,
  'power': 193,
  'program': 110,
  'didnt': 37,
  'case': 50,
  'different': 58,
  'little': 98,
  'however': 71,
  'law': 29,
  'best': 77,
  'long': 71,
  'probably': 96,
  'least': 73,
  'day': 32

## Predicting using the dictionary generated

In [45]:
Y_pred_own = predict(X_test_final, dictionary)

1
-219.35537187708667
-197.85335011629797
-221.7320126082388
-209.1248843057623
-227.3948123559305
-212.9702190332456
-210.85428571067587
-223.3329641023225
-220.07367925159573
-206.62762722416656
-198.61683840099298
-217.48696551251402
-222.28101315754856
-207.99989628777018
-187.98109644382959
-207.56058098190903
-205.6446357465906
-204.99342515904513
-195.57044608531993
-211.4688939478346
2
-223.82964258941672
-219.01229310950464
-237.6619492470698
-257.9224550191366
-243.07829475020603
-175.2071755817901
-223.9861568907777
-239.30014447751148
-232.28502848698128
-223.83970136957427
-237.91782668156128
-237.4818058904578
-246.65397495643256
-235.96601054293328
-234.87216589899558
-220.44987933054978
-222.58767899408434
-229.29477964599886
-220.0560774887543
-235.25685109832014
3
-279.90695550462095
-266.7984613098374
-271.1903685345951
-297.6906327989168
-244.1841437546994
-263.51161739364915
-274.4248009335097
-254.22929139484228
-253.0396700779542
-272.55938988745453
-277.86884333

-109.68810638582696
-111.58553070183862
-115.57429318726537
-109.21322358533413
-111.4768539352129
-110.32718294335507
-111.91749567660992
-115.41854075876448
-105.24953476817555
-115.01631976780288
-116.36130926410041
-116.07490813818839
-115.05613363582881
-117.33849216121641
-118.26472845464951
-114.46872811457428
-112.37386179096171
-113.11605737847475
-114.01541678535953
23
-608.0234288955031
-574.2484792860872
-588.7293651764586
-643.3553220028049
-589.9440404311887
-562.1321599635531
-591.3289959754868
-566.8156174155963
-509.1879971072871
-593.5373865580992
-625.4481631520865
-608.5754340737004
-599.3198414931993
-594.7181083631324
-617.078490823701
-587.2453881811156
-594.038067807807
-588.2974133899959
-582.0000238476701
-625.4534709889455
24
-1104.4814111742025
-971.5645003701758
-1152.7992118292884
-1236.42656239981
-1144.3409740079717
-970.8083550876382
-1041.2170671415167
-1120.3545044162997
-1127.4413456379898
-1049.8610431615755
-1133.2521621441563
-1149.6120824080251
-

-2378.709931217272
-2544.519683787979
-2397.4266239914336
-2142.9165364781675
-2123.723421705068
-2347.2566367297422
-2377.5814402910005
-2203.496122000203
-2337.6434491466694
-2331.143131491903
-2403.6341809283713
-2198.738308351493
-2292.8863863805964
-2150.2104213422754
-2095.051192849353
-1955.302514678966
-2074.0962661430012
-2325.3622332678083
44
-149.90309160563297
-140.78278973509748
-148.6224568749302
-157.04966813893637
-151.7735532076001
-153.32622802980802
-156.540527529174
-149.14830321039346
-153.84433490488055
-145.85782051217393
-155.4511810244734
-151.41395956053157
-143.33116077142753
-146.9918948817956
-148.1996808650347
-146.9265645181383
-146.49330075358318
-148.52639750762995
-147.03032377148588
-153.09935163104535
45
-91.11609734388469
-80.25204083738112
-93.35882572044159
-100.53981193204123
-93.06234037611164
-84.70889244229315
-89.3890512260994
-94.6263407346688
-92.35007401894927
-92.37520012207456
-84.03765293995212
-89.66935437764482
-93.26273272575887
-93.

-47.064851389330585
-38.31368079447233
-44.91328647304468
-40.94678329442457
-39.93188744274704
-43.97216837393344
-39.312135451481005
-40.891828228414234
-43.0568328646444
-45.44174356021979
-46.97599810884195
-37.93805906649647
-43.77404613311554
-45.20045747532164
-45.4238961364271
-45.57857678836828
-44.3060925506995
-46.7830599260566
-45.935454905644654
65
-2.9915402322817863
-2.9666209100569034
-2.978347428797223
-3.0239317280730216
-2.9915402322817863
-2.9995402749488624
-3.0035644252485882
-2.9968664765644606
-2.984922074439308
-2.9875640839021465
-2.978347428797223
-2.984922074439308
-3.0008798598779194
-3.0211920003319017
-2.998202482107202
-3.0103075391334784
-2.9995402749488624
-3.0103075391334784
-2.978347428797223
-3.0103075391334784
66
-781.3390026133461
-741.2129166709825
-793.3034134001581
-819.8529658305504
-792.7719248419515
-637.2604186125454
-751.9422023154322
-780.729547327357
-795.9281737820432
-779.0046620883172
-810.876260653038
-815.20314410373
-769.5349007927

-194.30320817266517
-190.10925282116813
-192.6561727944863
-172.36373103429423
-196.36811528445872
-194.0218370928003
-200.94283697123734
-173.3473544529856
-199.82067178906544
-194.10292617114402
-172.44173237839203
-187.71639499737455
-175.4212880030155
-193.04531760646313
86
-1100.6525888839408
-1030.8923005673494
-1053.1741122574633
-1156.5832851590503
-964.4958251311223
-1008.802187756843
-1071.4211678223935
-993.6588084763677
-994.4526326737238
-1049.1392994561268
-1138.302894298869
-1149.2489440011805
-1041.4577066411644
-1079.6329367008498
-1130.2570392465768
-1061.3932245442513
-1086.0132598529246
-1066.4866429209637
-1049.9630978860293
-1152.290969190911
87
-969.9396441141761
-788.8214956491928
-964.9258531422531
-1025.5390005812083
-963.974174719898
-871.0996565597496
-834.9000507368446
-923.9627947502644
-953.9490154881049
-892.2533314133225
-960.6225175743548
-930.8534181416181
-971.6222156919264
-896.6450731410997
-943.3294024354645
-830.7471551668092
-869.3443778782672
-

...

-218.23111370412877
-319.94556617184685
4898
-956.7389217991658
-845.011220368606
-977.6999521664997
-975.8431783591882
-966.4767253092824
-913.8875358914581
-917.875165899719
-933.9168236319902
-956.2906901131353
-891.5180885989187
-928.0249586917412
-858.8383014084345
-968.9416884536449
-923.5663136369657
-931.6102297168554
-916.5719678400603
-897.3535245423055
-907.070273636038
-876.9752607946667
-726.796950860796
4899
-420.60856364423375
-417.20856972701137
-402.60379125857384
-450.6904820576934
-383.0911676191946
-388.48646612909124
-417.4597507825058
-340.4923176582848
-363.33125888516787
-407.64512906159723
-440.24104762381535
-437.7945544176963
-399.3294685717303
-425.89005495302496
-436.1107934766512
-418.3247745204258
-415.7865225193892
-412.27793751878596
-416.4524892934956
-438.29517194827787
4900
-217.87461494412432
-168.0000477353445
-218.46875880780846
-229.87940941949012
-219.3798026974504
-201.03354396967745
-196.44223692768776
-213.85621936441106
-210.33858834213933
-

-630.3311806997431
4919
-381.6579063941006
-370.9970034727519
-403.57749616148504
-430.99196137743695
-409.47452740810127
-375.55258152770665
-400.89579411578706
-387.7185243575261
-387.91428882847487
-392.09385233339736
-409.6167300190643
-411.5531900644449
-399.18369508679774
-407.7746312752497
-404.510385862625
-392.67052986460715
-379.00864261131005
-405.02446673846345
-378.06775698903954
-418.7750511303774
4920
-1140.0605997354808
-932.0775026837039
-1130.3983724242873
-1227.6918430969874
-1135.0198531520766
-1031.9012143452032
-875.6290016494355
-1111.020364984237
-1132.3912707797494
-1066.8299475456408
-1097.075645982734
-1090.8443758716721
-1149.2349526848318
-1038.70621624463
-1103.996782960917
-886.1170005755872
-988.3823785334571
-914.6346263524327
-931.1475421275109
-1094.4560183947356
4921
-776.2827418348761
-597.603800374498
-778.5871541443356
-814.6699984829723
-774.1619221525731
-700.8422649903807
-667.056142250639
-764.4647420140177
-784.0380453339753
-705.981652997729

-179.87758459064818
-175.0211269499339
-188.21240339944418
4940
-2113.578133085105
-1547.530029626705
-2156.778279325577
-2196.323052430772
-2137.7472682360203
-1824.7164705183184
-1846.9349051978786
-2081.8138996534867
-2106.2216687326927
-1957.862127437086
-2073.953948711533
-2079.7047885332286
-2133.0916243833954
-1991.4282202645607
-2010.2566723566854
-1872.2834721895208
-1596.9841766590737
-1699.8360418067161
-1697.8727845845779
-2050.195971493063
4941
-116.49140837481647
-116.82880994817754
-120.6573943893186
-131.41371957613612
-124.99825064732812
-121.86709855833946
-124.4176125733032
-124.52503216188073
-123.5551851302407
-122.51099413012237
-116.35105323347565
-120.94118601162218
-122.32459868193098
-124.91632321215411
-113.12297847146581
-129.17705545170074
-121.13026408028867
-128.0253011859769
-120.96360709807234
-124.15467354152055
4942
-887.205890925074
-860.4616396799404
-922.187827345532
-939.5330003271371
-934.8901671739766
-907.6086665027444
-901.2674579344485
-922.0

-934.5489574713338
-956.0703875972694
-907.5054130369892
-946.2352723135803
-1062.063897688243
4961
-181.56314084550817
-173.5539633574065
-160.85578612855784
-194.50846149286602
-178.79854422101909
-178.8068480531921
-176.72545035711107
-175.65910963105352
-184.78526933621487
-182.08488322493614
-177.3600553038535
-191.16996983181843
-168.916078357476
-185.5974016787008
-178.27745881324142
-181.94852006165527
-180.3683585551475
-179.4200689486728
-172.808745642715
-191.14028278749885
4962
-85.19715949550339
-76.81992445560428
-81.43648869975144
-98.05665989651607
-87.35061504374221
-76.33900952088337
-74.1939147830328
-84.72700383359187
-85.03314172917948
-82.94026506363761
-84.5213819106719
-81.94398284436129
-86.47966262589557
-83.28913920090321
-85.07158256382533
-73.68912491287323
-81.23978161797932
-77.83917646053561
-81.15796579530557
-74.89133387699736
4963
-1098.3522456914081
-921.4544061028636
-1109.6096318771633
-1163.658123294606
-1116.9785007131732
-1026.7547929246266
-992

-326.3024549952175
-302.5205668324352
-310.9120125053698
-353.0532049773233
4982
-2547.600286779413
-2160.9817208584363
-2556.83407852276
-2797.654518432746
-2567.2895059604753
-2361.097153725963
-2047.6883565609978
-2493.4567255800575
-2491.274840553992
-2359.399639810069
-2516.6873829398046
-2456.0378704008444
-2575.6478179555643
-2330.0854915637738
-2485.138866872606
-1919.5193114939104
-2282.8946372965756
-2064.7644841341685
-2183.139303654911
-2477.328769969871
4983
-960.6085369789682
-757.5438120180409
-968.7418009000435
-997.2831809361865
-966.1117164656496
-862.7398057946692
-823.2112607404223
-933.2387620685257
-949.1675542433437
-867.0319952446124
-947.9391118618787
-940.5469843562088
-965.8556973897581
-890.158455487247
-925.9833385572949
-803.2692280163084
-829.2774032877296
-816.2022144222996
-687.1531041664612
-927.4713546011619
4984
-2576.684572859343
-2153.7756171925857
-2584.8482030434757
-2706.5941742621603
-2596.803042041774
-2337.9068470451853
-2120.02699824433
-249

In [46]:
Y_pred_own

['rec.autos',
 'sci.crypt',
 'comp.os.ms-windows.misc',
 'comp.graphics',
 'comp.graphics',
 'sci.electronics',
 'rec.sport.hockey',
 'comp.sys.ibm.pc.hardware',
 'sci.crypt',
 'comp.sys.mac.hardware',
 'rec.autos',
 'comp.graphics',
 'comp.sys.ibm.pc.hardware',
 'rec.motorcycles',
 'sci.med',
 'rec.sport.hockey',
 'comp.windows.x',
 'talk.politics.guns',
 'talk.politics.misc',
 'talk.politics.misc',
 'sci.space',
 'sci.space',
 'comp.windows.x',
 'sci.crypt',
 'sci.crypt',
 'talk.religion.misc',
 'talk.politics.guns',
 'talk.politics.misc',
 'comp.graphics',
 'rec.motorcycles',
 'talk.politics.guns',
 'sci.med',
 'talk.politics.guns',
 'comp.sys.ibm.pc.hardware',
 'sci.med',
 'talk.religion.misc',
 'sci.electronics',
 'comp.windows.x',
 'alt.atheism',
 'comp.windows.x',
 'comp.graphics',
 'talk.politics.misc',
 'talk.politics.misc',
 'talk.politics.misc',
 'talk.politics.misc',
 'talk.politics.misc',
 'rec.sport.hockey',
 'sci.electronics',
 'comp.sys.ibm.pc.hardware',
 'alt.atheism',

In [47]:
len(Y_pred_own)

5000

## Scoring and other metrics for self implementation

In [48]:
print(classification_report(Y_test, Y_pred_own))

                          precision    recall  f1-score   support

             alt.atheism       0.66      0.64      0.65       256
           comp.graphics       0.54      0.81      0.65       251
 comp.os.ms-windows.misc       0.88      0.54      0.67       247
comp.sys.ibm.pc.hardware       0.66      0.66      0.66       237
   comp.sys.mac.hardware       0.82      0.59      0.68       254
          comp.windows.x       0.79      0.76      0.77       242
            misc.forsale       0.92      0.42      0.58       271
               rec.autos       0.89      0.67      0.76       252
         rec.motorcycles       0.98      0.72      0.83       237
      rec.sport.baseball       0.98      0.83      0.89       242
        rec.sport.hockey       0.93      0.93      0.93       261
               sci.crypt       0.69      0.84      0.76       253
         sci.electronics       0.89      0.47      0.62       247
                 sci.med       0.91      0.72      0.80       269
         

In [49]:
print(confusion_matrix(Y_test, Y_pred_own))

[[163   0   0   0   0   0   0   0   0   0   0   2   0   3   0  22   0  30
   15  21]
 [  1 203   4   4   2   8   0   0   0   0   0   4   0   1   7   2   0   6
    7   2]
 [  2  30 133  20   1  28   0   0   0   1   0   8   0   0   2   0   0   1
   19   2]
 [  0  28   8 156   9   4   3   0   0   0   0  12   2   1   1   0   0   4
    9   0]
 [  0  30   2  22 149   1   1   1   0   0   0  14   1   2   2   0   1   9
   19   0]
 [  2  31   1   4   0 183   0   0   0   0   0   7   0   0   1   0   0   2
   10   1]
 [  0  20   3  20  13   1 114  14   1   1   3   9   7   3  13   0   4  18
   27   0]
 [  0   2   0   0   0   0   2 169   2   1   1   3   2   2   6   1   1  17
   43   0]
 [  0   0   0   0   0   1   3   2 171   0   0   1   2   1   1   0   2  17
   36   0]
 [  0   3   0   0   0   1   0   0   0 200  11   0   0   0   0   2   0  15
   10   0]
 [  0   0   0   1   0   1   0   0   0   2 244   0   0   0   0   0   0   6
    7   0]
 [  0   2   0   0   0   1   0   0   0   0   0 212   0   0   0   1

In [50]:
from sklearn.metrics import accuracy_score
print("Self implementation accuracy :" , accuracy_score(Y_test, Y_pred_own))
print("SKLearn accuracy :", accuracy_score(Y_test, Y_pred))

# adding some more block/stop words might help

Self implementation accuracy : 0.696
SKLearn accuracy : 0.8024
